##***Lectura y procesado de datos.***

####Conexión para leer base de datos en AWS RDS.

In [0]:
df = spark.read \
    .format("jdbc") \
    .option("url", "jdbc:mysql://db-train.ck6hmdu3rlig.eu-north-1.rds.amazonaws.com:3306/train_data") \
    .option("dbtable", "data") \
    .option("user", "admin") \
    .option("password", "TWOqDcKSMCsS3idI1kD5") \
    .load()

####Quitamos nulos del dataframe.

In [0]:
df_not_null = df.dropna(how="any")
df_not_null.show()

+--------------------+--------------------+-----+
|               title|                text|label|
+--------------------+--------------------+-----+
|LAW ENFORCEMENT O...|No comment is exp...|    1|
|                    |Did they post the...|    1|
|UNBELIEVABLE! OBA...| Now, most of the...|    1|
|Bobby Jindal, rai...|A dozen political...|    0|
|SATAN 2: Russia u...|The RS-28 Sarmat ...|    1|
|About Time! Chris...|All we can say on...|    1|
|DR BEN CARSON TAR...|DR. BEN CARSON TE...|    1|
|HOUSE INTEL CHAIR...|                    |    1|
|Sports Bar Owner ...|The owner of the ...|    1|
|Latest Pipeline L...|FILE – In this Se...|    1|
| GOP Senator Just...|The most punchabl...|    1|
|May Brexit offer ...|BRUSSELS (Reuters...|    0|
|Schumer calls on ...|WASHINGTON (Reute...|    0|
|WATCH: HILARIOUS ...|After watching th...|    1|
|No Change Expecte...|As more and more ...|    0|
|Billionaire Odebr...|RIO DE JANEIRO/SA...|    0|
|BRITISH WOMAN LOS...|Europe is likely ...|    1|


####Quitamos campos vacíos, no son nulos, cadenas de texto vacías.

In [0]:
mask = ((df_not_null.text != ' ') & (df_not_null.text != '')) & ((df_not_null.title != ' ') & (df_not_null.title != ''))
filtered_df = df_not_null.filter(mask)
display(filtered_df)

title text label LAW ENFORCEMENT ON HIGH ALERT Following Threats Against Cops And Whites On 9-11By #BlackLivesMatter And #FYF911 Terrorists [VIDEO] No comment is expected from Barack Obama Members of the #FYF911 or #FukYoFlag and #BlackLivesMatter movements called for the lynching and hanging of white people and cops. They encouraged others on a radio show Tuesday night to turn the tide and kill white people and cops to send a message about the killing of black people in America.One of the F***YoFlag organizers is called Sunshine. She has a radio blog show hosted from Texas called, Sunshine s F***ing Opinion Radio Show. A snapshot of her #FYF911 @LOLatWhiteFear Twitter page at 9:53 p.m. shows that she was urging supporters to Call now!! #fyf911 tonight we continue to dismantle the illusion of white Below is a SNAPSHOT Twitter Radio Call Invite #FYF911The radio show aired at 10:00 p.m. eastern standard time.During the show, callers clearly call for lynching and killing of white people.A 2:39 minute clip from the radio show can be heard here. It was provided to Breitbart Texas by someone who would like to be referred to as Hannibal. He has already received death threats as a result of interrupting #FYF911 conference calls.An unidentified black man said when those mother f**kers are by themselves, that s when when we should start f***ing them up. Like they do us, when a bunch of them ni**ers takin one of us out, that s how we should roll up. He said, Cause we already roll up in gangs anyway. There should be six or seven black mother f**ckers, see that white person, and then lynch their ass. Let s turn the tables. They conspired that if cops started losing people, then there will be a state of emergency. He speculated that one of two things would happen, a big-ass [R s?????] war, or ni**ers, they are going to start backin up. We are already getting killed out here so what the f**k we got to lose? Sunshine could be heard saying, Yep, that s true. That s so f**king true. He said, We need to turn the tables on them. Our kids are getting shot out here. Somebody needs to become a sacrifice on their side.He said, Everybody ain t down for that s**t, or whatever, but like I say, everybody has a different position of war. He continued, Because they don t give a f**k anyway. He said again, We might as well utilized them for that s**t and turn the tables on these n**ers. He said, that way we can start lookin like we ain t havin that many casualties, and there can be more causalities on their side instead of ours. They are out their killing black people, black lives don t matter, that s what those mother f**kers so we got to make it matter to them. Find a mother f**ker that is alone. Snap his ass, and then f***in hang him from a damn tree. Take a picture of it and then send it to the mother f**kers. We just need one example, and then people will start watchin . This will turn the tables on s**t, he said. He said this will start a trickle-down effect. He said that when one white person is hung and then they are just flat-hanging, that will start the trickle-down effect. He continued, Black people are good at starting trends. He said that was how to get the upper-hand. Another black man spoke up saying they needed to kill cops that are killing us. The first black male said, That will be the best method right there. Breitbart Texas previously reported how Sunshine was upset when racist white people infiltrated and disrupted one of her conference calls. She subsequently released the phone number of one of the infiltrators. The veteran immediately started receiving threatening calls.One of the #F***YoFlag movement supporters allegedly told a veteran who infiltrated their publicly posted conference call, We are going to rape and gut your pregnant wife, and your f***ing piece of sh*t unborn creature will be hung from a tree. Breitbart Texas previously encountered Sunshine at a Sandra Bland protest at the Waller County Jail in Texas, where she said a

####Comprobamos si las "clases" estan balanceadas.

In [0]:
filtered_df.groupBy("label").count().show()

+-----+-----+
|label|count|
+-----+-----+
|    1|35772|
|    0|35027|
+-----+-----+



####No hay mucho procesado que realizar.
#####Ahora nuestro "dataframe" procesado lo guardamos en un bucket de S3 en formato CSV, para que los encargados del modelo puedan acceder y coger estos datos para entrenar su modelo.

In [0]:
spark.conf.set("spark.hadoop.fs.s3a.region", "eu-north-1")
spark.sparkContext._jsc.hadoopConfiguration().set("fs.s3a.access.key", "ACCESS_KEY")
spark.sparkContext._jsc.hadoopConfiguration().set("fs.s3a.secret.key", "ACCESS_SECRET_KEY")

In [0]:
bucket_name = "bucket-train-data"
output_path = "s3a://{}/npl_data_4_train_csv".format(bucket_name)

filtered_df.write.csv(output_path, header=True, mode="overwrite")

#####Formato Parquet

In [0]:
bucket_name = "bucket-train-data"
output_path = "s3a://{}/npl_data_4_train_parquet/".format(bucket_name)

filtered_df.write.parquet(output_path, mode="overwrite")